In [1]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-

import os
import sys
import datetime as dt
from pathlib import Path

import numpy as np
import pandas as pd
import rasterio
from tqdm import tqdm

# ========= PATH CONFIG =========
CSV_IN_ROOT  = Path("/mnt/cephfs-mount/chenchen/CygnssDataCsvLand_full")
CSV_OUT_ROOT = Path("/mnt/cephfs-mount/chenchen/CygnssDataCsvLand_GWP")
GWP_ROOT     = Path("/mnt/cephfs-mount/chenchen/GlobalWaterPack")

# ========= GLOBAL WATERPACK AVAILABILITY =========
# 固定的 GWP 有效时间范围（按产品）
GWP_START_DATE = dt.date(2022, 1, 9)
GWP_END_DATE   = dt.date(2022, 12, 31)

# ========= 你想处理的时间段（自己改这里） =========
PROCESS_START_DATE = GWP_START_DATE
PROCESS_END_DATE   = GWP_END_DATE

# ========= SAMPLING CONFIG =========
SAMPLE_RATE = 0.015   # 先从 CSV 中抽样的比例：10% → 1/10
RANDOM_SEED = 42     # 随机种子，保证可复现


def get_date_from_filename(csv_path: Path):
    """Extract YYYYMMDD from filename like '20180901.csv' → datetime.date."""
    stem = csv_path.stem
    if len(stem) < 8:
        return None
    try:
        d = dt.datetime.strptime(stem[:8], "%Y%m%d").date()
        return d
    except Exception:
        return None


def build_gwp_paths(date_obj: dt.date):
    """Build paths to GWP main & obs files for a given date."""
    y = date_obj.year
    m = date_obj.month
    d = date_obj.day
    ymd = f"{y:04d}{m:02d}{d:02d}"

    gwp_dir = GWP_ROOT / f"{y:04d}" / f"{m:02d}" / f"{d:02d}"
    stem = f"GWP.OSWF.DAILY.{ymd}.v1"

    main_path = gwp_dir / f"{stem}.tif"
    obs_path  = gwp_dir / f"{stem}.obs.tif"
    return main_path, obs_path


def compute_water_fraction_for_row(
    row,
    arr_main: np.ndarray,
    arr_obs: np.ndarray,
    src_main: rasterio.io.DatasetReader,
    obs_nodata,
) -> float:
    """
    Compute GWP-based water fraction for a single CYGNSS observation.

    假设：
      - CSV 坐标是 lon/lat（EPSG:4326）
      - GWP tif 也是 EPSG:4326
      - OBS 语义：
          1   → water obs
          101 → land observation
          102 → ocean surface observation
          其它 / nodata → 不算观测

    步骤：
      - 用 c1..c4 的 lon/lat 构成矩形 footprint
      - 转成 raster row/col window
      - 要求 window 内所有 obs ∈ {1, 101, 102} 且 != nodata（full-obs）
      - 水像元定义为：main == 1 且 obs ∈ {1, 102}
      - water_fraction = 水像元数 / 总像元数（像元比例）
    """
    try:
        lons = [
            float(row.c1_lon), float(row.c2_lon),
            float(row.c3_lon), float(row.c4_lon),
        ]
        lats = [
            float(row.c1_lat), float(row.c2_lat),
            float(row.c3_lat), float(row.c4_lat),
        ]
    except AttributeError as e:
        raise KeyError(f"Missing corner columns in row: {e}")

    rows = []
    cols = []
    for lon, lat in zip(lons, lats):
        try:
            # EPSG:4326: index(lon, lat)
            r, c = src_main.index(lon, lat)
            rows.append(r)
            cols.append(c)
        except Exception:
            # 任一角点出界则丢掉
            return np.nan

    rmin = min(rows)
    rmax = max(rows)
    cmin = min(cols)
    cmax = max(cols)

    height, width = arr_main.shape
    if (rmax < 0 or rmin >= height or cmax < 0 or cmin >= width):
        # 完全在栅格外
        return np.nan

    rmin_c = max(rmin, 0)
    rmax_c = min(rmax, height - 1)
    cmin_c = max(cmin, 0)
    cmax_c = min(cmax, width - 1)

    if rmin_c > rmax_c or cmin_c > cmax_c:
        return np.nan

    sub_main = arr_main[rmin_c : rmax_c + 1, cmin_c : cmax_c + 1]
    sub_obs  = arr_obs[rmin_c : rmax_c + 1, cmin_c : cmax_c + 1]

    if sub_main.size == 0 or sub_obs.size == 0:
        return np.nan

    # ---- FULL OBS REQUIREMENT ----
    # 有效观测 obs: 1 (water), 101 (land obs), 102 (ocean obs)
    valid_obs_mask = np.isin(sub_obs, (1, 101, 102))
    if obs_nodata is not None:
        valid_obs_mask &= (sub_obs != obs_nodata)

    # footprint 里只要有一个像元不是有效观测，就直接丢掉
    if not np.all(valid_obs_mask):
        return np.nan

    # ---- WATER FRACTION (pixel fraction) ----
    # 水像元：main == 1 且 obs ∈ {1, 102}
    water_mask = (sub_main == 1) & np.isin(sub_obs, (1, 102))
    if water_mask.size == 0:
        return np.nan

    frac = float(water_mask.mean())  # 像元比例 0~1
    return frac


def process_one_csv(csv_in_path: Path):
    """Process a single daily CSV with GWP + pre-sampling + fraction."""
    date_obj = get_date_from_filename(csv_in_path)
    if date_obj is None:
        print(f"[WARN] Could not parse date from filename: {csv_in_path.name}, skipping.")
        return

    # 先按你设定的时间段过滤
    if date_obj < PROCESS_START_DATE or date_obj > PROCESS_END_DATE:
        return

    # 再看是否在 GWP 产品时间范围内
    if date_obj < GWP_START_DATE or date_obj > GWP_END_DATE:
        print(f"[INFO] {csv_in_path.name}: date {date_obj} outside GWP range, skipping.")
        return

    main_path, obs_path = build_gwp_paths(date_obj)
    if not main_path.exists() or not obs_path.exists():
        print(f"[WARN] Missing GWP files for {date_obj}:\n"
              f"   main: {main_path.exists()}  path={main_path}\n"
              f"   obs : {obs_path.exists()}  path={obs_path}\n"
              f"Skipping this CSV.")
        return

    # 输出路径（保持目录结构）
    rel = csv_in_path.relative_to(CSV_IN_ROOT)
    csv_out_path = CSV_OUT_ROOT / rel
    csv_out_path.parent.mkdir(parents=True, exist_ok=True)

    print(f"\n[INFO] === Processing {csv_in_path} (date {date_obj}) ===")
    df = pd.read_csv(csv_in_path, low_memory=False)

    required_cols = [
        "c1_lon", "c2_lon", "c3_lon", "c4_lon",
        "c1_lat", "c2_lat", "c3_lat", "c4_lat",
    ]
    for col in required_cols:
        if col not in df.columns:
            raise ValueError(f"Missing required column '{col}' in {csv_in_path}")

    # ====== 1. 先在 CSV 里抽样行，再算 GWP fraction ======
    n_total = len(df)
    n_keep  = max(int(n_total * SAMPLE_RATE), 1)
    df = df.sample(n=n_keep, random_state=RANDOM_SEED).reset_index(drop=True)
    print(f"[INFO] Pre-sampled rows: {n_total} → {len(df)} (rate ~{SAMPLE_RATE})")

    # ====== 2. 打开 GWP tif，一次读入内存 ======
    print(f"[INFO] Loading GWP rasters for {date_obj} ...")
    with rasterio.open(main_path) as src_main, rasterio.open(obs_path) as src_obs:
        if src_main.crs != src_obs.crs:
            raise ValueError(f"CRS mismatch between main and obs:\n"
                             f"  main: {src_main.crs}\n  obs : {src_obs.crs}")

        print(f"[INFO] Raster CRS: {src_main.crs}")

        arr_main = src_main.read(1)
        arr_obs  = src_obs.read(1)
        obs_nodata = src_obs.nodata

        print(f"[INFO] GWP shapes: main={arr_main.shape}, obs={arr_obs.shape}")
        print(f"[INFO] obs nodata: {obs_nodata}")

        n = len(df)
        water_frac = np.full(n, np.nan, dtype=np.float32)

        print(f"[INFO] Computing water_fraction_gwp for {n} sampled rows on {date_obj} ...")
        # 用 itertuples 比 iterrows 快一点
        for idx, row in enumerate(
            tqdm(
                df.itertuples(index=False),
                total=n,
                desc=f"{csv_in_path.stem}",   # e.g. "20180901"
                unit="row",
                leave=True,
            )
        ):
            wf = compute_water_fraction_for_row(
                row,
                arr_main,
                arr_obs,
                src_main,
                obs_nodata,
            )
            water_frac[idx] = wf

    df["water_fraction_gwp"] = water_frac

    # ====== 3. 过滤掉 full-obs 不满足的 footprint（NaN） ======
    before = len(df)
    df = df[~np.isnan(df["water_fraction_gwp"])].reset_index(drop=True)
    after = len(df)
    print(f"[INFO] Filtered rows by full-obs footprint: {before} → {after}")

    # ====== 4. 更新 water_fraction 列 ======
    if "water_fraction" in df.columns:
        if "water_fraction_orig" not in df.columns:
            df["water_fraction_orig"] = df["water_fraction"]
        df["water_fraction"] = df["water_fraction_gwp"]
        print("[INFO] Overwrote existing 'water_fraction' and backed up to 'water_fraction_orig'.")
    else:
        df["water_fraction"] = df["water_fraction_gwp"]
        print("[INFO] Created new 'water_fraction' column from GWP.")

    print(f"[INFO] Writing output to: {csv_out_path}")
    df.to_csv(csv_out_path, index=False)


def main():
    print(f"[INFO] Input root         : {CSV_IN_ROOT}")
    print(f"[INFO] Output root        : {CSV_OUT_ROOT}")
    print(f"[INFO] GWP root           : {GWP_ROOT}")
    print(f"[INFO] GWP date range     : {GWP_START_DATE} → {GWP_END_DATE}")
    print(f"[INFO] Process date range : {PROCESS_START_DATE} → {PROCESS_END_DATE}")
    print(f"[INFO] Sampling rate      : {SAMPLE_RATE} (keep ~1 out of {int(1/SAMPLE_RATE)})")
    print()

    if not CSV_IN_ROOT.exists():
        print(f"[ERROR] Input root does not exist: {CSV_IN_ROOT}")
        return

    csv_files = sorted(CSV_IN_ROOT.rglob("*.csv"))
    if not csv_files:
        print("[ERROR] No CSV files found under input root.")
        return

    # 只保留在处理时间段内的文件
    candidate_files = []
    for p in csv_files:
        d = get_date_from_filename(p)
        if d is None:
            continue
        if PROCESS_START_DATE <= d <= PROCESS_END_DATE:
            candidate_files.append(p)

    print(f"[INFO] Found {len(csv_files)} CSV files in total.")
    print(f"[INFO] {len(candidate_files)} CSV files in selected period.")
    print()

    for csv_path in tqdm(candidate_files, desc="Days", unit="day"):
        try:
            process_one_csv(csv_path)
        except Exception as e:
            print(f"[ERROR] Failed to process {csv_path}: {e}")

    print("\n[INFO] All done.")


# ====== 在 Jupyter 里直接跑 main() ======
main()

[INFO] Input root         : /mnt/cephfs-mount/chenchen/CygnssDataCsvLand_full
[INFO] Output root        : /mnt/cephfs-mount/chenchen/CygnssDataCsvLand_GWP
[INFO] GWP root           : /mnt/cephfs-mount/chenchen/GlobalWaterPack
[INFO] GWP date range     : 2022-01-09 → 2022-12-31
[INFO] Process date range : 2022-01-09 → 2022-12-31
[INFO] Sampling rate      : 0.015 (keep ~1 out of 66)

[INFO] Found 2526 CSV files in total.
[INFO] 357 CSV files in selected period.



Days:   0%|                                                                                                          | 0/357 [00:00<?, ?day/s]


[INFO] === Processing /mnt/cephfs-mount/chenchen/CygnssDataCsvLand_full/2022_01_v3/20220109.csv (date 2022-01-09) ===
[INFO] Pre-sampled rows: 1494600 → 22419 (rate ~0.015)
[INFO] Loading GWP rasters for 2022-01-09 ...
[INFO] Raster CRS: EPSG:4326
[INFO] GWP shapes: main=(86400, 172800), obs=(86400, 172800)
[INFO] obs nodata: 255.0
[INFO] Computing water_fraction_gwp for 22419 sampled rows on 2022-01-09 ...



20220109: 100%|██████████████████████████████████████████████████████████████████████████████████████| 22419/22419 [00:06<00:00, 3412.01row/s]


[INFO] Filtered rows by full-obs footprint: 22419 → 19635
[INFO] Created new 'water_fraction' column from GWP.
[INFO] Writing output to: /mnt/cephfs-mount/chenchen/CygnssDataCsvLand_GWP/2022_01_v3/20220109.csv


...


[INFO] === Processing /mnt/cephfs-mount/chenchen/CygnssDataCsvLand_full/2022_12_v3/20221231.csv (date 2022-12-31) ===
[INFO] Pre-sampled rows: 1304489 → 19567 (rate ~0.015)
[INFO] Loading GWP rasters for 2022-12-31 ...
[INFO] Raster CRS: EPSG:4326
[INFO] GWP shapes: main=(86400, 172800), obs=(86400, 172800)
[INFO] obs nodata: 255.0
[INFO] Computing water_fraction_gwp for 19567 sampled rows on 2022-12-31 ...



20221231: 100%|██████████████████████████████████████████████████████████████████████████████████████| 19567/19567 [00:04<00:00, 4089.55row/s]


[INFO] Filtered rows by full-obs footprint: 19567 → 16938
[INFO] Created new 'water_fraction' column from GWP.
[INFO] Writing output to: /mnt/cephfs-mount/chenchen/CygnssDataCsvLand_GWP/2022_12_v3/20221231.csv


Days: 100%|████████████████████████████████████████████████████████████████████████████████████████████| 357/357 [19:03:04<00:00, 192.11s/day]


[INFO] All done.


In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-

import os
import sys
import datetime as dt
from pathlib import Path

import numpy as np
import pandas as pd
import rasterio
from tqdm import tqdm

# ========= PATH CONFIG =========
CSV_IN_ROOT  = Path("/mnt/cephfs-mount/chenchen/CygnssDataCsvLand_full")
CSV_OUT_ROOT = Path("/mnt/cephfs-mount/chenchen/CygnssDataCsvLand_GWP")
GWP_ROOT     = Path("/mnt/cephfs-mount/chenchen/GlobalWaterPack")

# ========= GLOBAL WATERPACK AVAILABILITY =========
# 固定的 GWP 有效时间范围（按产品）
GWP_START_DATE = dt.date(2020, 1, 1)
GWP_END_DATE   = dt.date(2020, 7, 31)

# ========= 你想处理的时间段（自己改这里） =========
PROCESS_START_DATE = GWP_START_DATE
PROCESS_END_DATE   = GWP_END_DATE

# ========= SAMPLING CONFIG =========
SAMPLE_RATE = 0.1   # 先从 CSV 中抽样的比例：10% → 1/10
RANDOM_SEED = 42     # 随机种子，保证可复现


def get_date_from_filename(csv_path: Path):
    """Extract YYYYMMDD from filename like '20180901.csv' → datetime.date."""
    stem = csv_path.stem
    if len(stem) < 8:
        return None
    try:
        d = dt.datetime.strptime(stem[:8], "%Y%m%d").date()
        return d
    except Exception:
        return None


def build_gwp_paths(date_obj: dt.date):
    """Build paths to GWP main & obs files for a given date."""
    y = date_obj.year
    m = date_obj.month
    d = date_obj.day
    ymd = f"{y:04d}{m:02d}{d:02d}"

    gwp_dir = GWP_ROOT / f"{y:04d}" / f"{m:02d}" / f"{d:02d}"
    stem = f"GWP.OSWF.DAILY.{ymd}.v1"

    main_path = gwp_dir / f"{stem}.tif"
    obs_path  = gwp_dir / f"{stem}.obs.tif"
    return main_path, obs_path


def compute_water_fraction_for_row(
    row,
    arr_main: np.ndarray,
    arr_obs: np.ndarray,
    src_main: rasterio.io.DatasetReader,
    obs_nodata,
) -> float:
    """
    Compute GWP-based water fraction for a single CYGNSS observation.

    假设：
      - CSV 坐标是 lon/lat（EPSG:4326）
      - GWP tif 也是 EPSG:4326
      - OBS 语义：
          1   → water obs
          101 → land observation
          102 → ocean surface observation
          其它 / nodata → 不算观测

    步骤：
      - 用 c1..c4 的 lon/lat 构成矩形 footprint
      - 转成 raster row/col window
      - 要求 window 内所有 obs ∈ {1, 101, 102} 且 != nodata（full-obs）
      - 水像元定义为：main == 1 且 obs ∈ {1, 102}
      - water_fraction = 水像元数 / 总像元数（像元比例）
    """
    try:
        lons = [
            float(row.c1_lon), float(row.c2_lon),
            float(row.c3_lon), float(row.c4_lon),
        ]
        lats = [
            float(row.c1_lat), float(row.c2_lat),
            float(row.c3_lat), float(row.c4_lat),
        ]
    except AttributeError as e:
        raise KeyError(f"Missing corner columns in row: {e}")

    rows = []
    cols = []
    for lon, lat in zip(lons, lats):
        try:
            # EPSG:4326: index(lon, lat)
            r, c = src_main.index(lon, lat)
            rows.append(r)
            cols.append(c)
        except Exception:
            # 任一角点出界则丢掉
            return np.nan

    rmin = min(rows)
    rmax = max(rows)
    cmin = min(cols)
    cmax = max(cols)

    height, width = arr_main.shape
    if (rmax < 0 or rmin >= height or cmax < 0 or cmin >= width):
        # 完全在栅格外
        return np.nan

    rmin_c = max(rmin, 0)
    rmax_c = min(rmax, height - 1)
    cmin_c = max(cmin, 0)
    cmax_c = min(cmax, width - 1)

    if rmin_c > rmax_c or cmin_c > cmax_c:
        return np.nan

    sub_main = arr_main[rmin_c : rmax_c + 1, cmin_c : cmax_c + 1]
    sub_obs  = arr_obs[rmin_c : rmax_c + 1, cmin_c : cmax_c + 1]

    if sub_main.size == 0 or sub_obs.size == 0:
        return np.nan

    # ---- FULL OBS REQUIREMENT ----
    # 有效观测 obs: 1 (water), 101 (land obs), 102 (ocean obs)
    valid_obs_mask = np.isin(sub_obs, (1, 101, 102))
    if obs_nodata is not None:
        valid_obs_mask &= (sub_obs != obs_nodata)

    # footprint 里只要有一个像元不是有效观测，就直接丢掉
    if not np.all(valid_obs_mask):
        return np.nan

    # ---- WATER FRACTION (pixel fraction) ----
    # 水像元：main == 1 且 obs ∈ {1, 102}
    water_mask = (sub_main == 1) & np.isin(sub_obs, (1, 102))
    if water_mask.size == 0:
        return np.nan

    frac = float(water_mask.mean())  # 像元比例 0~1
    return frac


def process_one_csv(csv_in_path: Path):
    """Process a single daily CSV with GWP + pre-sampling + fraction."""
    date_obj = get_date_from_filename(csv_in_path)
    if date_obj is None:
        print(f"[WARN] Could not parse date from filename: {csv_in_path.name}, skipping.")
        return

    # 先按你设定的时间段过滤
    if date_obj < PROCESS_START_DATE or date_obj > PROCESS_END_DATE:
        return

    # 再看是否在 GWP 产品时间范围内
    if date_obj < GWP_START_DATE or date_obj > GWP_END_DATE:
        print(f"[INFO] {csv_in_path.name}: date {date_obj} outside GWP range, skipping.")
        return

    main_path, obs_path = build_gwp_paths(date_obj)
    if not main_path.exists() or not obs_path.exists():
        print(f"[WARN] Missing GWP files for {date_obj}:\n"
              f"   main: {main_path.exists()}  path={main_path}\n"
              f"   obs : {obs_path.exists()}  path={obs_path}\n"
              f"Skipping this CSV.")
        return

    # 输出路径（保持目录结构）
    rel = csv_in_path.relative_to(CSV_IN_ROOT)
    csv_out_path = CSV_OUT_ROOT / rel
    csv_out_path.parent.mkdir(parents=True, exist_ok=True)

    print(f"\n[INFO] === Processing {csv_in_path} (date {date_obj}) ===")
    df = pd.read_csv(csv_in_path, low_memory=False)

    required_cols = [
        "c1_lon", "c2_lon", "c3_lon", "c4_lon",
        "c1_lat", "c2_lat", "c3_lat", "c4_lat",
    ]
    for col in required_cols:
        if col not in df.columns:
            raise ValueError(f"Missing required column '{col}' in {csv_in_path}")

    # ====== 1. 先在 CSV 里抽样行，再算 GWP fraction ======
    n_total = len(df)
    n_keep  = max(int(n_total * SAMPLE_RATE), 1)
    df = df.sample(n=n_keep, random_state=RANDOM_SEED).reset_index(drop=True)
    print(f"[INFO] Pre-sampled rows: {n_total} → {len(df)} (rate ~{SAMPLE_RATE})")

    # ====== 2. 打开 GWP tif，一次读入内存 ======
    print(f"[INFO] Loading GWP rasters for {date_obj} ...")
    with rasterio.open(main_path) as src_main, rasterio.open(obs_path) as src_obs:
        if src_main.crs != src_obs.crs:
            raise ValueError(f"CRS mismatch between main and obs:\n"
                             f"  main: {src_main.crs}\n  obs : {src_obs.crs}")

        print(f"[INFO] Raster CRS: {src_main.crs}")

        arr_main = src_main.read(1)
        arr_obs  = src_obs.read(1)
        obs_nodata = src_obs.nodata

        print(f"[INFO] GWP shapes: main={arr_main.shape}, obs={arr_obs.shape}")
        print(f"[INFO] obs nodata: {obs_nodata}")

        n = len(df)
        water_frac = np.full(n, np.nan, dtype=np.float32)

        print(f"[INFO] Computing water_fraction_gwp for {n} sampled rows on {date_obj} ...")
        # 用 itertuples 比 iterrows 快一点
        for idx, row in enumerate(
            tqdm(
                df.itertuples(index=False),
                total=n,
                desc=f"{csv_in_path.stem}",   # e.g. "20180901"
                unit="row",
                leave=True,
            )
        ):
            wf = compute_water_fraction_for_row(
                row,
                arr_main,
                arr_obs,
                src_main,
                obs_nodata,
            )
            water_frac[idx] = wf

    df["water_fraction_gwp"] = water_frac

    # ====== 3. 过滤掉 full-obs 不满足的 footprint（NaN） ======
    before = len(df)
    df = df[~np.isnan(df["water_fraction_gwp"])].reset_index(drop=True)
    after = len(df)
    print(f"[INFO] Filtered rows by full-obs footprint: {before} → {after}")

    # ====== 4. 更新 water_fraction 列 ======
    if "water_fraction" in df.columns:
        if "water_fraction_orig" not in df.columns:
            df["water_fraction_orig"] = df["water_fraction"]
        df["water_fraction"] = df["water_fraction_gwp"]
        print("[INFO] Overwrote existing 'water_fraction' and backed up to 'water_fraction_orig'.")
    else:
        df["water_fraction"] = df["water_fraction_gwp"]
        print("[INFO] Created new 'water_fraction' column from GWP.")

    print(f"[INFO] Writing output to: {csv_out_path}")
    df.to_csv(csv_out_path, index=False)


def main():
    print(f"[INFO] Input root         : {CSV_IN_ROOT}")
    print(f"[INFO] Output root        : {CSV_OUT_ROOT}")
    print(f"[INFO] GWP root           : {GWP_ROOT}")
    print(f"[INFO] GWP date range     : {GWP_START_DATE} → {GWP_END_DATE}")
    print(f"[INFO] Process date range : {PROCESS_START_DATE} → {PROCESS_END_DATE}")
    print(f"[INFO] Sampling rate      : {SAMPLE_RATE} (keep ~1 out of {int(1/SAMPLE_RATE)})")
    print()

    if not CSV_IN_ROOT.exists():
        print(f"[ERROR] Input root does not exist: {CSV_IN_ROOT}")
        return

    csv_files = sorted(CSV_IN_ROOT.rglob("*.csv"))
    if not csv_files:
        print("[ERROR] No CSV files found under input root.")
        return

    # 只保留在处理时间段内的文件
    candidate_files = []
    for p in csv_files:
        d = get_date_from_filename(p)
        if d is None:
            continue
        if PROCESS_START_DATE <= d <= PROCESS_END_DATE:
            candidate_files.append(p)

    print(f"[INFO] Found {len(csv_files)} CSV files in total.")
    print(f"[INFO] {len(candidate_files)} CSV files in selected period.")
    print()

    for csv_path in tqdm(candidate_files, desc="Days", unit="day"):
        try:
            process_one_csv(csv_path)
        except Exception as e:
            print(f"[ERROR] Failed to process {csv_path}: {e}")

    print("\n[INFO] All done.")


# ====== 在 Jupyter 里直接跑 main() ======
main()